In [10]:
from IPython.display import display, Image, clear_output

In [11]:
#Import all the necessary libraries
import pymzml
import csv
import os
import pandas as pd
import numpy as np
import math
from matplotlib import pyplot as plt
import re
import plotly.express as px
from collections import defaultdict

import plotly.io as pio
import json
import plotly.graph_objs as go
import matplotlib.colors as mcolors

import json
import ipywidgets as widgets

import warnings

import time
##Custom scripts
# from OzESI_parsing_function_old import *

# from plotting_functions import *

# dfdfplotting_functions


No module named 'ms_deisotope._c.averagine' averagine
No module named 'ms_deisotope._c.scoring'
No module named 'ms_deisotope._c.deconvoluter_base'
No module named 'ms_deisotope._c.deconvoluter_base'
No module named 'ms_deisotope._c.deconvoluter_base'


In [12]:
### Filter for o3on and o2only
# path to Projects/04_29_23/mzml folder

import os
import shutil
print(os.getcwd())
# Set the source directory where the files are located
src_directory = "Projects/04_29_23/mzml/" # For example, '/path/to/your/files'

# Set the destination directories for o3on and o2only
dst_directory_o3on = os.path.join(src_directory, "o3on")
dst_directory_o2only = os.path.join(src_directory, "o2only")

# Create the destination directories if they don't exist
os.makedirs(dst_directory_o3on, exist_ok=True)
os.makedirs(dst_directory_o2only, exist_ok=True)

# Loop through the files in the source directory
for filename in os.listdir(src_directory):
    # Check if the file ends with ".mzML"
    if filename.endswith(".mzML"):
        # Determine which folder to move the file to based on its name
        if "_o3on.mzML" in filename:
            shutil.move(os.path.join(src_directory, filename), os.path.join(dst_directory_o3on, filename))
        elif "_o2only.mzML" in filename:
            shutil.move(os.path.join(src_directory, filename), os.path.join(dst_directory_o2only, filename))





/home/sanjay/github/lipids/Lipidomics/lipid_platform


In [13]:
#OLD WAY
###Importing Variables for all functions

# data_base_name_location = 'lipid_database/Lipid_Database.xlsx'####Lipid database with Standard Carnitines
# mzml_folder = './data_mzml/04-29-2023_mzml/test_oz_1/'
# tolerance = 0.3
# remove_std = True

# # Example usage:
# folder_name_to_save = 'TEST_04-29-2023_validation_test_6'
# file_name_to_save = 'TEST_04-29-2023_validation_test_6'
# save_data= True



# # Example usage:

# file_name_to_save = 'TEST_04-29-2023_validation_test_2'
# save_data= True

data_base_name_location = 'lipid_database/Lipid_Database.xlsx'####Lipid database with Standard Carnitines
#NEW WAY
Pre_folder = './Projects/'
Project_Folder =Pre_folder + '04_29_23/mzml/o3on/'
folder_name_to_save = 'Projects/04_29_23/results/'
file_name_to_save = '04_29_23'


tolerance = 0.3
remove_std = True
save_data= True


In [14]:
# folder_name_to_save = Project_Folder+ 'Processed Results/'
# data_base_name_location = 'lipid_database/Lipid_Database.xlsx'
# mzml_folder = Project_Folder +"mzml/"
# Pre_edge_r_path = Project_Folder+"Pre_EdgeR/"
# plots_2_save_path = Project_Folder+"Plots/"
# label_file = Project_Folder+"Labels/labels.csv"

# ##Labels DF and Labels List
# labels_df = pd.read_csv(label_file)
# labels_list = list(labels_df)
# labels_list = labels_list +["Class","Lipid"]

In [15]:

###All functions

#Function to read in MRM database
#Option to remove STDs from database##Not finished need option to use another database with no qualitative ACs


def read_mrm_list(filename,remove_std = True):
    mrm_list_new = pd.read_excel(filename, sheet_name=None)
    mrm_list_new = pd.concat(mrm_list_new, ignore_index=True)
    mrm_list_offical = mrm_list_new[['Compound Name', 'Parent Ion', 'Product Ion', 'Class']]
    # Add underscore to middle of columns names
    mrm_list_offical.columns = mrm_list_offical.columns.str.replace(' ', '_')
    # Round Parent Ion and Product Ion to 1 decimal place
    mrm_list_offical['Parent_Ion'] = np.round(mrm_list_offical['Parent_Ion'],1)
    mrm_list_offical['Product_Ion'] = np.round(mrm_list_offical['Product_Ion'],1)
    # Create transition column by combining Parent Ion and Product Ion with arrow between numbers
    mrm_list_offical['Transition'] = mrm_list_offical['Parent_Ion'].astype(str) + ' -> ' + mrm_list_offical['Product_Ion'].astype(str)
    # Change column compound name to lipid
    mrm_list_offical = mrm_list_offical.rename(columns={'Compound_Name': 'Lipid'})
    # Make a column called Class match lipid column to lipid types
    if remove_std == True:
        lipid_class = mrm_list_offical['Class'].unique()
        lipid_class_to_keep = ['PS','PG','CE','PC', 'DAG', 'PE', 'TAG', 'FA', 'Cer', 'CAR', 'PI','SM']
        mrm_list_offical = mrm_list_offical[mrm_list_offical['Class'].isin(lipid_class_to_keep)]
    return mrm_list_offical


# Function to create an ion dictionary from an MRM database DataFrame
def create_ion_dict(mrm_database):
    ion_dict = defaultdict(list)
    # Iterate through the rows of the MRM database DataFrame
    for index, row in mrm_database.iterrows():
        # Add a tuple with Lipid and Class to the ion dictionary using Parent_Ion and Product_Ion as the key
        ion_dict[(row['Parent_Ion'], row['Product_Ion'])].append((row['Lipid'], row['Class']))
    return ion_dict

### New way to parse OzESI data
OzESI_time_df = pd.DataFrame(columns=['Lipid', 'Parent_Ion', 'Product_Ion', 'Intensity', 'Transition', 'Class', 'Sample_ID', 'Retention_Time', 'OzESI_Intensity'])

# def mzml_parser(file_name):
#     global OzESI_time_df  # Declare OzESI_time_df as a global variable
    
#     df = pd.DataFrame(columns=['Lipid', 'Parent_Ion', 'Product_Ion', 'Intensity', 'Transition', 'Class', 'Sample_ID'])
#     data_folder = os.listdir(file_name)
#     data_folder.sort()
#     path_to_mzml_files = file_name

#     for file in data_folder:
#         if file.endswith('.mzML'):
#             run = pymzml.run.Reader(path_to_mzml_files + file, skip_chromatogram=False)
#             df_all = pd.DataFrame(columns=['Lipid', 'Parent_Ion', 'Product_Ion', 'Intensity', 'Transition', 'Class', 'Sample_ID'])
#             q1_mz = 0
#             q3_mz = 0
#             count = 0

#             for spectrum in run:
#                 for element in spectrum.ID.split(' '):
#                     intensity_store = np.array([])
                    
#                     if 'Q1' in element:
#                         q1 = element.split('=')
#                         q1_mz = np.round(float(q1[1]), 1)
                    
#                     if 'Q3' in element:
#                         q3 = element.split('=')
#                         q3_mz = np.round(float(q3[1]), 1)
#                         for time, intensity in spectrum.peaks():
#                             row = {
#                                 'Parent_Ion': q1_mz,
#                                 'Product_Ion': q3_mz,
#                                 'Retention_Time': time,
#                                 'OzESI_Intensity': intensity
#                             }
#                             row['Sample_ID'] = file[:-5]
#                             row['Transition'] = str(row['Parent_Ion']) + ' -> ' + str(row['Product_Ion'])
#                             OzESI_time_df = OzESI_time_df.append(row, ignore_index=True)
                        
#                         for mz, intensity in spectrum.peaks():
#                             intensity_store = np.append(intensity_store, intensity)

#                         intensity_sum = np.sum(intensity_store)
#                         df_all.loc[count, 'Parent_Ion'] = q1_mz
#                         df_all.loc[count, 'Product_Ion'] = q3_mz
#                         df_all.loc[count, 'Parent_Ion'] = np.round(df_all.loc[count, 'Parent_Ion'], 1)
#                         df_all.loc[count, 'Product_Ion'] = np.round(df_all.loc[count, 'Product_Ion'], 1)
#                         df_all.loc[count, 'Intensity'] = intensity_sum
#                         df_all.loc[count, 'Transition'] = f"{q1_mz} -> {q3_mz}"
#                         df_all.loc[count, 'Sample_ID'] = file[:-5]
#                         count += 1

#             df = df.append(df_all, ignore_index=True)
#     print('Finished parsing mzML files' + '\n')
#     # print file name to make sure it is working
#     print(file_name)
#     return df

def mzml_parser(file_name):
    global OzESI_time_df  # Declare OzESI_time_df as a global variable
    
    rows = []
    ozesi_rows = []
    
    data_folder = os.listdir(file_name)
    data_folder.sort()
    path_to_mzml_files = file_name

    for file in data_folder:
        if file.endswith('.mzML'):
            run = pymzml.run.Reader(path_to_mzml_files + file, skip_chromatogram=False)
            q1_mz = 0
            q3_mz = 0

            for spectrum in run:
                for element in spectrum.ID.split(' '):
                    
                    if 'Q1' in element:
                        q1 = element.split('=')
                        q1_mz = np.round(float(q1[1]), 1)
                    
                    if 'Q3' in element:
                        q3 = element.split('=')
                        q3_mz = np.round(float(q3[1]), 1)
                        
                        intensity_store = np.array([intensity for _, intensity in spectrum.peaks()])
                        intensity_sum = np.sum(intensity_store)
                        
                        transition = f"{q1_mz} -> {q3_mz}"
                        sample_id = file[:-5]
                        
                        rows.append({
                            'Parent_Ion': q1_mz,
                            'Product_Ion': q3_mz,
                            'Intensity': intensity_sum,
                            'Transition': transition,
                            'Sample_ID': sample_id
                        })
                        
                        for time, intensity in spectrum.peaks():
                            ozesi_rows.append({
                                'Parent_Ion': q1_mz,
                                'Product_Ion': q3_mz,
                                'Retention_Time': time,
                                'OzESI_Intensity': intensity,
                                'Sample_ID': sample_id,
                                'Transition': transition
                            })

    df = pd.DataFrame(rows)
    OzESI_time_df = pd.DataFrame(ozesi_rows)
    print('Finished parsing mzML files\n')
    return df


# Function to check if the absolute difference between two values is within a given tolerance
def within_tolerance(a, b, tolerance=0.3):
    return abs(a - b) <= tolerance

# Function to match the ions in a DataFrame row with the ions in an ion dictionary
def match_ions(row, ion_dict, tolerance=0.3):
    ions = (row['Parent_Ion'], row['Product_Ion'])
    matched_lipids = []
    matched_classes = []

    # Iterate through the ion dictionary
    for key, value in ion_dict.items():
        # Check if both the Parent_Ion and Product_Ion values are within the specified tolerance
        if within_tolerance(ions[0], key[0], tolerance) and within_tolerance(ions[1], key[1], tolerance):
            # If within tolerance, extend the matched_lipids and matched_classes lists with the corresponding values
            matched_lipids.extend([match[0] for match in value])
            matched_classes.extend([match[1] for match in value])

    # If any matches were found, update the Lipid and Class columns in the row
    if matched_lipids and matched_classes:
        row['Lipid'] = ' | '.join(matched_lipids)
        row['Class'] = ' | '.join(matched_classes)

    return row

####Combined functions for Matching

def match_lipids_parser(mrm_database,df, tolerance=0.3):
    ion_dict = create_ion_dict(mrm_database)
    # Assuming you have the df DataFrame to apply the match_ions function
    df_matched = df.apply(lambda row: match_ions(row, ion_dict=ion_dict, tolerance=tolerance), axis=1)


    # df_matched = df_matched.dropna()
    
    return df_matched


def save_dataframe(df, folder_name, file_name, max_attempts=5):
    folder_path = f'data_results/data/data_matching/{folder_name}'
    os.makedirs(folder_path, exist_ok=True)

    for i in range(max_attempts):
        file_path = f'{folder_path}/{file_name}.csv'
        if not os.path.isfile(file_path):
            df.to_csv(file_path, index=False)
            print(f"Saved DataFrame to {file_path}")
            break
    else:
        print(f"Failed to save DataFrame after {max_attempts} attempts.")
        return None


def full_parse(data_base_name_location,mzml_folder, folder_name_to_save, file_name_to_save,tolerance,remove_std = True,
               save_data=False):
    mrm_database = read_mrm_list(data_base_name_location,remove_std=remove_std)
    df = mzml_parser(mzml_folder)
    df_matched = match_lipids_parser(mrm_database,df, tolerance=tolerance)
    
    if save_data == True:
        
        save_dataframe(df_matched, folder_name_to_save, file_name_to_save)

    return df_matched





In [16]:
df_matched = full_parse(data_base_name_location,Project_Folder, folder_name_to_save, 
                        file_name_to_save,tolerance, remove_std = remove_std,save_data=save_data)



/tmp/ipykernel_10679/2473317584.py:14: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_10679/2473317584.py:15: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_10679/2473317584.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Finished parsing mzML files

Failed to save DataFrame after 5 attempts.


In [17]:

df_matched.head(None)
OzESI_time_df.head(None)



Parent_Ion  Product_Ion  Retention_Time  OzESI_Intensity  \
0            694.6        547.6        0.118533       254.960022   
1            694.6        547.6        0.240367       239.120010   
2            694.6        547.6        0.362183       260.560028   
3            694.6        547.6        0.484017       330.260010   
4            694.6        547.6        0.605833       353.880035   
...            ...          ...             ...              ...   
222712       902.8        603.6       19.614183     18169.841797   
222713       902.8        603.6       19.736000     18471.162109   
222714       902.8        603.6       19.857833     17463.300781   
222715       902.8        603.6       19.979650     18173.921875   
222716       902.8        603.6       20.101483     17947.060547   

                               Sample_ID      Transition  
0       DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6  
1       DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6  
2       DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6  
3       DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6  
4       DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6  
...                                  ...             ...  
222712  FAD189_Ms-5xFAD-hippoTG18-1_o3on  902.8 -> 603.6  
222713  FAD189_Ms-5xFAD-hippoTG18-1_o3on  902.8 -> 603.6  
222714  FAD189_Ms-5xFAD-hippoTG18-1_o3on  902.8 -> 603.6  
222715  FAD189_Ms-5xFAD-hippoTG18-1_o3on  902.8 -> 603.6  
222716  FAD189_Ms-5xFAD-hippoTG18-1_o3on  902.8 -> 603.6  

[222717 rows x 6 columns]

In [18]:
mrm_database = read_mrm_list(data_base_name_location)
tolerance = 0.3
df_oz_matched = match_lipids_parser(mrm_database, OzESI_time_df, tolerance)


/tmp/ipykernel_10679/2473317584.py:14: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_10679/2473317584.py:15: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_10679/2473317584.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [19]:
df_oz_matched.tail(50)
# #print to excel
# df_oz_matched.to_excel("OzESI_time_df_04_29_23.xlsx")

Class                        Lipid  OzESI_Intensity  Parent_Ion  \
222667   TAG  [TG(55:10),TG(54:3)]_FA18:1      4010.380371       902.8   
222668   TAG  [TG(55:10),TG(54:3)]_FA18:1      3524.860352       902.8   
222669   TAG  [TG(55:10),TG(54:3)]_FA18:1      4105.120117       902.8   
222670   TAG  [TG(55:10),TG(54:3)]_FA18:1     33123.503906       902.8   
222671   TAG  [TG(55:10),TG(54:3)]_FA18:1    172018.765625       902.8   
222672   TAG  [TG(55:10),TG(54:3)]_FA18:1    175727.187500       902.8   
222673   TAG  [TG(55:10),TG(54:3)]_FA18:1    128808.812500       902.8   
222674   TAG  [TG(55:10),TG(54:3)]_FA18:1     79138.046875       902.8   
222675   TAG  [TG(55:10),TG(54:3)]_FA18:1     55040.562500       902.8   
222676   TAG  [TG(55:10),TG(54:3)]_FA18:1     39817.484375       902.8   
222677   TAG  [TG(55:10),TG(54:3)]_FA18:1     33702.863281       902.8   
222678   TAG  [TG(55:10),TG(54:3)]_FA18:1     27446.621094       902.8   
222679   TAG  [TG(55:10),TG(54:3)]_FA18:1     25236.021484       902.8   
222680   TAG  [TG(55:10),TG(54:3)]_FA18:1     30696.322266       902.8   
222681   TAG  [TG(55:10),TG(54:3)]_FA18:1     71206.382812       902.8   
222682   TAG  [TG(55:10),TG(54:3)]_FA18:1     48768.402344       902.8   
222683   TAG  [TG(55:10),TG(54:3)]_FA18:1     33026.242188       902.8   
222684   TAG  [TG(55:10),TG(54:3)]_FA18:1     26851.142578       902.8   
222685   TAG  [TG(55:10),TG(54:3)]_FA18:1     23391.361328       902.8   
222686   TAG  [TG(55:10),TG(54:3)]_FA18:1     21760.521484       902.8   
222687   TAG  [TG(55:10),TG(54:3)]_FA18:1     21566.501953       902.8   
222688   TAG  [TG(55:10),TG(54:3)]_FA18:1     19709.980469       902.8   
222689   TAG  [TG(55:10),TG(54:3)]_FA18:1     18855.800781       902.8   
222690   TAG  [TG(55:10),TG(54:3)]_FA18:1     18885.742188       902.8   
222691   TAG  [TG(55:10),TG(54:3)]_FA18:1     18906.601562       902.8   
222692   TAG  [TG(55:10),TG(54:3)]_FA18:1     18366.001953       902.8   
222693   TAG  [TG(55:10),TG(54:3)]_FA18:1     17095.621094       902.8   
222694   TAG  [TG(55:10),TG(54:3)]_FA18:1     16866.640625       902.8   
222695   TAG  [TG(55:10),TG(54:3)]_FA18:1     17478.501953       902.8   
222696   TAG  [TG(55:10),TG(54:3)]_FA18:1     16924.740234       902.8   
222697   TAG  [TG(55:10),TG(54:3)]_FA18:1     17142.841797       902.8   
222698   TAG  [TG(55:10),TG(54:3)]_FA18:1     16554.001953       902.8   
222699   TAG  [TG(55:10),TG(54:3)]_FA18:1     15659.041016       902.8   
222700   TAG  [TG(55:10),TG(54:3)]_FA18:1     16174.401367       902.8   
222701   TAG  [TG(55:10),TG(54:3)]_FA18:1     16060.960938       902.8   
222702   TAG  [TG(55:10),TG(54:3)]_FA18:1     15850.401367       902.8   
222703   TAG  [TG(55:10),TG(54:3)]_FA18:1     16764.820312       902.8   
222704   TAG  [TG(55:10),TG(54:3)]_FA18:1     16395.140625       902.8   
222705   TAG  [TG(55:10),TG(54:3)]_FA18:1     16887.900391       902.8   
222706   TAG  [TG(55:10),TG(54:3)]_FA18:1     17335.781250       902.8   
222707   TAG  [TG(55:10),TG(54:3)]_FA18:1     17019.001953       902.8   
222708   TAG  [TG(55:10),TG(54:3)]_FA18:1     17684.742188       902.8   
222709   TAG  [TG(55:10),TG(54:3)]_FA18:1     17559.242188       902.8   
222710   TAG  [TG(55:10),TG(54:3)]_FA18:1     17944.820312       902.8   
222711   TAG  [TG(55:10),TG(54:3)]_FA18:1     18003.421875       902.8   
222712   TAG  [TG(55:10),TG(54:3)]_FA18:1     18169.841797       902.8   
222713   TAG  [TG(55:10),TG(54:3)]_FA18:1     18471.162109       902.8   
222714   TAG  [TG(55:10),TG(54:3)]_FA18:1     17463.300781       902.8   
222715   TAG  [TG(55:10),TG(54:3)]_FA18:1     18173.921875       902.8   
222716   TAG  [TG(55:10),TG(54:3)]_FA18:1     17947.060547       902.8   

        Product_Ion  Retention_Time                         Sample_ID  \
222667        603.6       14.131983  FAD189_Ms-5xFAD-hippoTG18-1_o3on   
222668        603.6       14.253817  FAD189_Ms-5xFAD-hippoTG18-1_o3on   
222669       

In [20]:
#### Filter retention times

filtered_df = df_oz_matched[(df_oz_matched['Retention_Time'] > 10.0) & (df_oz_matched['Retention_Time'] < 16.0)]
filtered_df['Retention_Time'] = filtered_df['Retention_Time'].round(2)
filtered_df['OzESI_Intensity'] = filtered_df['OzESI_Intensity'].round(0)
# Assuming the DataFrame is named df

# Keep only unique combinations of 'Sample_ID' and 'Transition'
#filtered_df = filtered_df.drop_duplicates(subset=['Sample_ID', 'Transition'])


#filtered_df = filtered_df.groupby('Transition').apply(lambda x: x.loc[x['OzESI_Intensity'].idxmax()]).reset_index(drop=True)
filtered_df = filtered_df.groupby(['Sample_ID', 'Transition']).apply(lambda x: x.loc[x['OzESI_Intensity'].idxmax()]).reset_index(drop=True)
filtered_df.tail(100)


/tmp/ipykernel_10679/3316649919.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_10679/3316649919.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Class                        Lipid  OzESI_Intensity  Parent_Ion  \
1340   NaN                          NaN           9851.0       740.8   
1341   NaN                          NaN            337.0       746.8   
1342   NaN                          NaN            269.0       748.8   
1343   NaN                          NaN            698.0       750.8   
1344   NaN                          NaN            668.0       762.7   
...    ...                          ...              ...         ...   
1435   TAG  [TG(53:10),TG(52:3)]_FA18:1          40842.0       874.8   
1436   TAG   [TG(53:9),TG(52:2)]_FA18:1         333856.0       876.8   
1437   TAG            [TG(54:5)]_FA18:1           4512.0       898.8   
1438   TAG  [TG(55:11),TG(54:4)]_FA18:1          31386.0       900.8   
1439   TAG  [TG(55:10),TG(54:3)]_FA18:1         175727.0       902.8   

      Product_Ion  Retention_Time                         Sample_ID  \
1340        551.6           14.95  FAD189_M2-5xFAD-diencTG18-1_o3on   
1341        599.6           13.12  FAD189_M2-5xFAD-diencTG18-1_o3on   
1342        601.6           11.29  FAD189_M2-5xFAD-diencTG18-1_o3on   
1343        603.6           10.31  FAD189_M2-5xFAD-diencTG18-1_o3on   
1344        573.6           12.63  FAD189_M2-5xFAD-diencTG18-1_o3on   
...           ...             ...                               ...   
1435        575.6           13.66  FAD189_Ms-5xFAD-hippoTG18-1_o3on   
1436        577.6           14.87  FAD189_Ms-5xFAD-hippoTG18-1_o3on   
1437        599.6           12.43  FAD189_Ms-5xFAD-hippoTG18-1_o3on   
1438        601.6           13.53  FAD189_Ms-5xFAD-hippoTG18-1_o3on   
1439        603.6           14.74  FAD189_Ms-5xFAD-hippoTG18-1_o3on   

          Transition  
1340  740.8 -> 551.6  
1341  746.8 -> 599.6  
1342  748.8 -> 601.6  
1343  750.8 -> 603.6  
1344  762.7 -> 573.6  
...              ...  
1435  874.8 -> 575.6  
1436  876.8 -> 577.6  
1437  898.8 -> 599.6  
1438  900.8 -> 601.6  
1439  902.8 -> 603.6  

[100 rows x 8 columns]

In [21]:
#Create df_matched_2 and concat df_matched and filtered_df
df_matched_2 = pd.concat([df_matched, filtered_df[['Retention_Time', 'OzESI_Intensity']]], axis=1)


In [22]:
df_matched_2.tail(5)

Class     Intensity                        Lipid  Parent_Ion  \
1435   TAG  6.787187e+05  [TG(53:10),TG(52:3)]_FA18:1       874.8   
1436   TAG  3.647270e+06   [TG(53:9),TG(52:2)]_FA18:1       876.8   
1437   TAG  1.356127e+05            [TG(54:5)]_FA18:1       898.8   
1438   TAG  3.820187e+05  [TG(55:11),TG(54:4)]_FA18:1       900.8   
1439   TAG  1.658646e+06  [TG(55:10),TG(54:3)]_FA18:1       902.8   

      Product_Ion                         Sample_ID      Transition  \
1435        575.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  874.8 -> 575.6   
1436        577.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  876.8 -> 577.6   
1437        599.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  898.8 -> 599.6   
1438        601.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  900.8 -> 601.6   
1439        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  902.8 -> 603.6   

      Retention_Time  OzESI_Intensity  
1435           13.66          40842.0  
1436           14.87         333856.0  
1437           12.43           4512.0  
1438           13.53          31386.0  
1439           14.74         175727.0

In [23]:
# Create a new DataFrame to store the DB_Position and Aldehyde_Ion values
df_DB_position = pd.DataFrame(columns=['DB_Position','Aldehyde_Ion'])

# Loop over the range of DB_Position values and calculate the corresponding Aldehyde_Ion values
for i in range(3, 21):
    df_DB_position.loc[i,'DB_Position'] = i
    df_DB_position.loc[i,'Aldehyde_Ion'] = 26 + (14 * (i-3)) 

# df_DB_position.head(None)

OzESI_list = [7,9,12]

for i in OzESI_list:
        # Retrieve the Aldehyde_Ion value for the current DB_Position
        aldehyde_ion = df_DB_position.loc[df_DB_position["DB_Position"] == i, "Aldehyde_Ion"].values[0]
        
        # Calculate n-i values
        df_matched_2["n-{}".format(i)] = df_matched_2["Parent_Ion"] - aldehyde_ion

df_matched_2.head(None)


Class     Intensity                        Lipid  Parent_Ion  \
0      NaN  2.567996e+05                          NaN       694.6   
1      NaN  2.185144e+05                          NaN       696.6   
2      NaN  6.608002e+06                          NaN       698.7   
3      NaN  7.330655e+04                          NaN       720.6   
4      NaN  1.428391e+05                          NaN       722.6   
...    ...           ...                          ...         ...   
1435   TAG  6.787187e+05  [TG(53:10),TG(52:3)]_FA18:1       874.8   
1436   TAG  3.647270e+06   [TG(53:9),TG(52:2)]_FA18:1       876.8   
1437   TAG  1.356127e+05            [TG(54:5)]_FA18:1       898.8   
1438   TAG  3.820187e+05  [TG(55:11),TG(54:4)]_FA18:1       900.8   
1439   TAG  1.658646e+06  [TG(55:10),TG(54:3)]_FA18:1       902.8   

      Product_Ion                         Sample_ID      Transition  \
0           547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1           549.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  696.6 -> 549.6   
2           551.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  698.7 -> 551.6   
3           573.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  720.6 -> 573.6   
4           575.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  722.6 -> 575.6   
...           ...                               ...             ...   
1435        575.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  874.8 -> 575.6   
1436        577.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  876.8 -> 577.6   
1437        599.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  898.8 -> 599.6   
1438        601.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  900.8 -> 601.6   
1439        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  902.8 -> 603.6   

      Retention_Time  OzESI_Intensity    n-7    n-9   n-12  
0              11.69           3903.0  612.6  584.6  542.6  
1              12.91          18586.0  614.6  586.6  544.6  
2              14.00          59211.0  616.7  588.7  546.7  
3              13.63            590.0  638.6  610.6  568.6  
4              12.77           3643.0  640.6  612.6  570.6  
...              ...              ...    ...    ...    ...  
1435           13.66          40842.0  792.8  764.8  722.8  
1436           14.87         333856.0  794.8  766.8  724.8  
1437           12.43           4512.0  816.8  788.8  746.8  
1438           13.53          31386.0  818.8  790.8  748.8  
1439           14.74         175727.0  820.8  792.8  750.8  

[1440 rows x 12 columns]

In [24]:
#Make a new column for Labels of n-#
df_matched_2['Labels'] = ''
OzESI_list = [7, 9, 12]

def within_tolerance(a, b, tolerance=0.3):
    return abs(a - b) <= tolerance
columns = [
    'Lipid', 'Parent_Ion', 'Product_Ion', 'Intensity', 'Transition', 'Class',
    'Sample_ID', 'Retention_Time', 'Intensity_OzESI', 'Mean_Retention_Time',
    'Mean_Intensity_OzESI', 'n-7', 'n-9', 'n-12', 'Labels'
]
df_OzESI_n = pd.DataFrame(columns=columns)

# def add_lipid_info(df_matched_2, OzESI_list, tolerance=0.3):
#     df_test = df_matched_2.copy()
#     df_test_2 = df_matched_2.copy()
#     global df_OzESI_n
#     for i in OzESI_list:
#         df_test['n-' + str(i)] = df_test['n-' + str(i)].astype(float)
    
#     for i in range(len(df_test)):
#         if pd.isna(df_test.loc[i, 'Lipid']):
#             parent_ion = df_test.loc[i, 'Parent_Ion']
            
#             for j in range(len(df_test)):
#                 row_data = df_test.loc[j].copy()
#                 if within_tolerance(parent_ion, row_data['n-7'], tolerance) and isinstance(row_data['Lipid'], str):
#                     df_test.loc[i, 'Lipid'] = row_data['Lipid']
#                     df_test.loc[i, 'Labels'] = 'n-7' + row_data['Labels']
                    
#                     # Append to df_OzESI_n
#                     appended_row = df_test.loc[i].copy()
#                     appended_row['Labels'] = 'n-7' + row_data['Labels']
#                     df_OzESI_n = df_OzESI_n.append(appended_row, ignore_index=True)
                    
#                 elif within_tolerance(parent_ion, row_data['n-9'], tolerance) and isinstance(row_data['Lipid'], str):
#                     df_test.loc[i, 'Lipid'] = row_data['Lipid']
#                     df_test.loc[i, 'Labels'] = 'n-9' + row_data['Labels']
                    
#                     # Append to df_OzESI_n
#                     appended_row = df_test.loc[i].copy()
#                     appended_row['Labels'] = 'n-9' + row_data['Labels']
#                     df_OzESI_n = df_OzESI_n.append(appended_row, ignore_index=True)
                    
#                 elif within_tolerance(parent_ion, row_data['n-12'], tolerance) and isinstance(row_data['Lipid'], str):
#                     df_test.loc[i, 'Lipid'] = row_data['Lipid']
#                     df_test.loc[i, 'Labels'] = 'n-12' + row_data['Labels']
                    
#                     # Append to df_OzESI_n
#                     appended_row = df_test.loc[i].copy()
#                     appended_row['Labels'] = 'n-12' + row_data['Labels']
#                     df_OzESI_n = df_OzESI_n.append(appended_row, ignore_index=True)
    
#     df_test.dropna(subset=['Lipid'], inplace=True)
#     return df_test

#Function to add lipid name
def add_lipid_info(df_matched_2, OzESI_list, tolerance=0.3):
    df_test = df_matched_2.copy()
    df_test_2 = df_matched_2.copy()
    global df_OzESI_n
    
    for i in OzESI_list:
        df_test['n-' + str(i)] = df_test['n-' + str(i)].astype(float)
    
    for i in range(len(df_test)):
        if pd.isna(df_test.loc[i, 'Lipid']):
            parent_ion = df_test.loc[i, 'Parent_Ion']
            
            for j in range(len(df_test)):
                row_data = df_test.loc[j].copy()
                if within_tolerance(parent_ion, row_data['n-7'], tolerance) and isinstance(row_data['Lipid'], str):
                    df_test.loc[i, 'Lipid'] = row_data['Lipid']
                    df_test.loc[i, 'Labels'] = 'n-7' + row_data['Labels']
                    
                    # Append to df_test_2
                    appended_row = df_test.loc[i].copy()
                    appended_row['Labels'] = 'n-7' + row_data['Labels']
                    df_test_2 = df_test_2.append(appended_row, ignore_index=True)
                    
                elif within_tolerance(parent_ion, row_data['n-9'], tolerance) and isinstance(row_data['Lipid'], str):
                    df_test.loc[i, 'Lipid'] = row_data['Lipid']
                    df_test.loc[i, 'Labels'] = 'n-9' + row_data['Labels']
                    
                    # Append to df_test_2
                    appended_row = df_test.loc[i].copy()
                    appended_row['Labels'] = 'n-9' + row_data['Labels']
                    df_test_2 = df_test_2.append(appended_row, ignore_index=True)
                    
                elif within_tolerance(parent_ion, row_data['n-12'], tolerance) and isinstance(row_data['Lipid'], str):
                    df_test.loc[i, 'Lipid'] = row_data['Lipid']
                    df_test.loc[i, 'Labels'] = 'n-12' + row_data['Labels']
                    
                    # Append to df_test_2
                    appended_row = df_test.loc[i].copy()
                    appended_row['Labels'] = 'n-12' + row_data['Labels']
                    df_test_2 = df_test_2.append(appended_row, ignore_index=True)
    
    df_test_2.dropna(subset=['Lipid'], inplace=True)
    return df_test_2


In [25]:
#Add lipid name to df_matched 3
df_matched_3 = add_lipid_info(df_matched_2, OzESI_list, tolerance=0.3)

/tmp/ipykernel_10679/2444659214.py:97: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/tmp/ipykernel_10679/2444659214.py:88: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/tmp/ipykernel_10679/2444659214.py:79: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



In [26]:
df_matched_3.head(None) 

Class     Intensity                        Lipid  Parent_Ion  \
27      TAG  6.869138e+05            [TG(50:3)]_FA18:1       846.8   
28      TAG  3.262575e+06   [TG(51:9),TG(50:2)]_FA18:1       848.8   
29      TAG  8.906404e+06   [TG(51:8),TG(50:1)]_FA18:1       850.8   
30      TAG  7.219475e+05            [TG(52:4)]_FA18:1       872.8   
31      TAG  4.364672e+06  [TG(53:10),TG(52:3)]_FA18:1       874.8   
...     ...           ...                          ...         ...   
58995   NaN  7.496407e+04  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58996   NaN  7.496407e+04  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58997   NaN  7.496407e+04  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58998   NaN  7.496407e+04  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58999   NaN  7.496407e+04  [TG(55:10),TG(54:3)]_FA18:1       820.8   

       Product_Ion                         Sample_ID      Transition  \
27           547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  846.8 -> 547.6   
28           549.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  848.8 -> 549.6   
29           551.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  850.8 -> 551.6   
30           573.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  872.8 -> 573.6   
31           575.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  874.8 -> 575.6   
...            ...                               ...             ...   
58995        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58996        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58997        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58998        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58999        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   

       Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels  
27              12.58          72587.0  764.8  736.8  694.8         
28              13.79         409651.0  766.8  738.8  696.8         
29              15.13        2236988.0  768.8  740.8  698.8         
30              12.57         159733.0  790.8  762.8  720.8         
31              13.66         928619.0  792.8  764.8  722.8         
...               ...              ...    ...    ...    ...    ...  
58995           14.65           1985.0  738.8  710.8  668.8    n-7  
58996           14.65           1985.0  738.8  710.8  668.8    n-7  
58997           14.65           1985.0  738.8  710.8  668.8    n-7  
58998           14.65           1985.0  738.8  710.8  668.8    n-7  
58999           14.65           1985.0  738.8  710.8  668.8    n-7  

[57920 rows x 13 columns]

In [27]:
#Filter n-7 and n-9 and match their retention times

# Create an empty list to store the valid rows
valid_rows = []

# Iterate over each combination of Lipid and Sample_ID
for _, group_df in df_matched_3.groupby(['Lipid', 'Sample_ID']):
    # Check if both n-7 and n-9 labels exist in the group
    if 'n-7' in group_df['Labels'].values and 'n-9' in group_df['Labels'].values:
        # Get the retention times for n-7 and n-9 labels
        retention_n7 = group_df.loc[group_df['Labels'] == 'n-7', 'Retention_Time'].values[0]
        retention_n9 = group_df.loc[group_df['Labels'] == 'n-9', 'Retention_Time'].values[0]
        
        # Compare the retention times within the tolerance
        if abs(retention_n7 - retention_n9) <= 0.4:
            valid_rows.append(group_df)

# Combine the valid rows into a new DataFrame
df_matched_3_valid = pd.concat(valid_rows)

# Print the resulting DataFrame
df_matched_3_valid.head(None)


Class      Intensity                        Lipid  Parent_Ion  \
99      TAG  295729.101242            [TG(50:3)]_FA18:1       846.8   
4242    NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
4243    NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
4244    NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
4245    NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
...     ...            ...                          ...         ...   
50117   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
50118   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
50119   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
50120   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
50121   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   

       Product_Ion                         Sample_ID      Transition  \
99           547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  846.8 -> 547.6   
4242         547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
4243         547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
4244         547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
4245         547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
...            ...                               ...             ...   
50117        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
50118        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
50119        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
50120        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
50121        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   

       Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels  
99              12.58           9707.0  764.8  736.8  694.8         
4242            11.94            923.0  612.6  584.6  542.6   n-12  
4243            11.94            923.0  612.6  584.6  542.6   n-12  
4244            11.94            923.0  612.6  584.6  542.6   n-12  
4245            11.94            923.0  612.6  584.6  542.6   n-12  
...               ...              ...    ...    ...    ...    ...  
50117           11.49            561.0  736.8  708.8  666.8    n-7  
50118           11.49            561.0  736.8  708.8  666.8    n-7  
50119           11.49            561.0  736.8  708.8  666.8    n-7  
50120           11.49            561.0  736.8  708.8  666.8    n-7  
50121           11.49            561.0  736.8  708.8  666.8    n-7  

[9006 rows x 13 columns]

In [28]:
# Create a new DataFrame with rows within the tolerance
df_matched_3_RT = df_matched_3_valid.copy()

# Iterate over each combination of Lipid and Sample_ID
for _, group_df in df_matched_3_RT.groupby(['Lipid', 'Sample_ID']):
    # Check if both n-7 and n-9 labels exist in the group
    if 'n-7' in group_df['Labels'].values and 'n-9' in group_df['Labels'].values:
        # Get the retention times for n-7 and n-9 labels
        retention_n7 = group_df.loc[group_df['Labels'] == 'n-7', 'Retention_Time'].values[0]
        retention_n9 = group_df.loc[group_df['Labels'] == 'n-9', 'Retention_Time'].values[0]
        
        # Compare the retention times within the tolerance
        if abs(retention_n7 - retention_n9) > 0.4:
            # Drop rows that don't meet the tolerance
            indices_to_drop = group_df.index
            df_matched_3_RT = df_matched_3_RT.drop(indices_to_drop)

# Reset the index of the filtered DataFrame
df_matched_3_RT = df_matched_3_RT.reset_index(drop=True)

# Print the filtered DataFrame
df_matched_3_RT.head(None)


Class      Intensity                        Lipid  Parent_Ion  \
0      TAG  295729.101242            [TG(50:3)]_FA18:1       846.8   
1      NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
2      NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
3      NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
4      NaN  116301.908737            [TG(50:3)]_FA18:1       694.6   
...    ...            ...                          ...         ...   
9001   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
9002   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
9003   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
9004   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   
9005   NaN   41575.322960  [TG(55:11),TG(54:4)]_FA18:1       818.8   

      Product_Ion                         Sample_ID      Transition  \
0           547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  846.8 -> 547.6   
1           547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
2           547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
3           547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
4           547.6  DOD93_F4-5xFAD-Dienc_TG18-1_o3on  694.6 -> 547.6   
...           ...                               ...             ...   
9001        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
9002        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
9003        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
9004        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   
9005        601.6    FAD189_F3-WT-cortexTG18-1_o3on  818.8 -> 601.6   

      Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels  
0              12.58           9707.0  764.8  736.8  694.8         
1              11.94            923.0  612.6  584.6  542.6   n-12  
2              11.94            923.0  612.6  584.6  542.6   n-12  
3              11.94            923.0  612.6  584.6  542.6   n-12  
4              11.94            923.0  612.6  584.6  542.6   n-12  
...              ...              ...    ...    ...    ...    ...  
9001           11.49            561.0  736.8  708.8  666.8    n-7  
9002           11.49            561.0  736.8  708.8  666.8    n-7  
9003           11.49            561.0  736.8  708.8  666.8    n-7  
9004           11.49            561.0  736.8  708.8  666.8    n-7  
9005           11.49            561.0  736.8  708.8  666.8    n-7  

[9006 rows x 13 columns]

In [29]:
#sorting df matched (BUT THIS IS OFF ON RT)

df_matched_3_sorted = df_matched_3.sort_values(by=['Sample_ID','Product_Ion'])
#drop duplicates Lipid and Labels
#df_matched_3_sorted = df_matched_3_sorted.drop_duplicates()
#df_matched_3_sorted = df_matched_3_sorted.drop_duplicates(subset=['Lipid','Labels'], keep='first')
df_matched_3_sorted.head(None)


Class      Intensity                        Lipid  Parent_Ion  \
27      TAG  686913.811157            [TG(50:3)]_FA18:1       846.8   
1440    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1441    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1442    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1443    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
...     ...            ...                          ...         ...   
58995   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58996   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58997   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58998   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58999   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   

       Product_Ion                         Sample_ID      Transition  \
27           547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  846.8 -> 547.6   
1440         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1441         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1442         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1443         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
...            ...                               ...             ...   
58995        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58996        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58997        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58998        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58999        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   

       Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels  
27              12.58          72587.0  764.8  736.8  694.8         
1440            11.69           3903.0  612.6  584.6  542.6   n-12  
1441            11.69           3903.0  612.6  584.6  542.6   n-12  
1442            11.69           3903.0  612.6  584.6  542.6   n-12  
1443            11.69           3903.0  612.6  584.6  542.6   n-12  
...               ...              ...    ...    ...    ...    ...  
58995           14.65           1985.0  738.8  710.8  668.8    n-7  
58996           14.65           1985.0  738.8  710.8  668.8    n-7  
58997           14.65           1985.0  738.8  710.8  668.8    n-7  
58998           14.65           1985.0  738.8  710.8  668.8    n-7  
58999           14.65           1985.0  738.8  710.8  668.8    n-7  

[57920 rows x 13 columns]

In [30]:
#sorting df matched (BUT THIS IS OFF ON RT)

df_matched_3_sorted_rt = df_matched_3_RT.sort_values(by=['Sample_ID','Product_Ion'])
#drop duplicates Lipid and Labels
#df_matched_3_sorted_rt = df_matched_3_sorted_rt.drop_duplicates()
df_matched_3_sorted_rt = df_matched_3_sorted_rt.drop_duplicates(subset=['Lipid','Labels','Sample_ID'], keep='first')
df_matched_3_sorted_rt.head(None)


Class     Intensity                       Lipid  Parent_Ion  Product_Ion  \
4630   TAG  3.262575e+06  [TG(51:9),TG(50:2)]_FA18:1       848.8        549.6   
4631   NaN  2.185144e+05  [TG(51:9),TG(50:2)]_FA18:1       696.6        549.6   
4671   NaN  4.582103e+05  [TG(51:9),TG(50:2)]_FA18:1       738.7        549.6   
4711   NaN  3.307983e+05  [TG(51:9),TG(50:2)]_FA18:1       766.7        549.6   
4025   TAG  8.906404e+06  [TG(51:8),TG(50:1)]_FA18:1       850.8        551.6   
...    ...           ...                         ...         ...          ...   
7893   NaN  3.612916e+04           [TG(54:5)]_FA18:1       816.8        599.6   
3864   TAG  1.983536e+05           [TG(50:3)]_FA18:1       846.8        547.6   
3865   NaN  8.817191e+04           [TG(50:3)]_FA18:1       694.6        547.6   
3905   NaN  4.825633e+05           [TG(50:3)]_FA18:1       736.7        547.6   
3945   NaN  9.380160e+05           [TG(50:3)]_FA18:1       764.7        547.6   

                             Sample_ID      Transition  Retention_Time  \
4630  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  848.8 -> 549.6           13.79   
4631  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  696.6 -> 549.6           12.91   
4671  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  738.7 -> 549.6           13.74   
4711  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  766.7 -> 549.6           13.71   
4025  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  850.8 -> 551.6           15.13   
...                                ...             ...             ...   
7893     FAD189_M3-WT-diencTG18-1_o3on  816.8 -> 599.6           12.34   
3864  FAD189_Ms-5xFAD-hippoTG18-1_o3on  846.8 -> 547.6           12.58   
3865  FAD189_Ms-5xFAD-hippoTG18-1_o3on  694.6 -> 547.6           11.69   
3905  FAD189_Ms-5xFAD-hippoTG18-1_o3on  736.7 -> 547.6           15.94   
3945  FAD189_Ms-5xFAD-hippoTG18-1_o3on  764.7 -> 547.6           15.79   

      OzESI_Intensity    n-7    n-9   n-12 Labels  
4630         409651.0  766.8  738.8  696.8         
4631          18586.0  614.6  586.6  544.6   n-12  
4671          49935.0  656.7  628.7  586.7    n-9  
4711          15393.0  684.7  656.7  614.7    n-7  
4025        2236988.0  768.8  740.8  698.8         
...               ...    ...    ...    ...    ...  
7893            350.0  734.8  706.8  664.8    n-7  
3864           4758.0  764.8  736.8  694.8         
3865            820.0  612.6  584.6  542.6   n-12  
3905           4474.0  654.7  626.7  584.7    n-9  
3945           8868.0  682.7  654.7  612.7    n-7  

[242 rows x 13 columns]

In [31]:
df_matched_3_sorted_rt.to_excel("df_matched_3_sorted_rt_04_29_23.xlsx")

In [32]:
df_matched_3_sorted.head(None)

Class      Intensity                        Lipid  Parent_Ion  \
27      TAG  686913.811157            [TG(50:3)]_FA18:1       846.8   
1440    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1441    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1442    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1443    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
...     ...            ...                          ...         ...   
58995   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58996   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58997   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58998   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58999   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   

       Product_Ion                         Sample_ID      Transition  \
27           547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  846.8 -> 547.6   
1440         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1441         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1442         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1443         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
...            ...                               ...             ...   
58995        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58996        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58997        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58998        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58999        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   

       Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels  
27              12.58          72587.0  764.8  736.8  694.8         
1440            11.69           3903.0  612.6  584.6  542.6   n-12  
1441            11.69           3903.0  612.6  584.6  542.6   n-12  
1442            11.69           3903.0  612.6  584.6  542.6   n-12  
1443            11.69           3903.0  612.6  584.6  542.6   n-12  
...               ...              ...    ...    ...    ...    ...  
58995           14.65           1985.0  738.8  710.8  668.8    n-7  
58996           14.65           1985.0  738.8  710.8  668.8    n-7  
58997           14.65           1985.0  738.8  710.8  668.8    n-7  
58998           14.65           1985.0  738.8  710.8  668.8    n-7  
58999           14.65           1985.0  738.8  710.8  668.8    n-7  

[57920 rows x 13 columns]

In [33]:
#def compute_intensity_ratio(df):

# df_matched_4 = df_matched_3.copy()  # make a copy of the dataframe to avoid changing the original one
# df['Ratio'] = None  # initially set all ratios to None
# unique_lipids = df['Lipid'].unique()
# for lipid in unique_lipids:
#     lipid_rows = df[df['Lipid'] == lipid]
#     if 'n-7' in lipid_rows['Labels'].values and 'n-9' in lipid_rows['Labels'].values:
#         # check if the 'Sample_ID' values are the same for 'n-7' and 'n-9' lipid rows
#         sample_id_n7 = lipid_rows[lipid_rows['Labels'] == 'n-7']['Sample_ID'].values[0]
#         sample_id_n9 = lipid_rows[lipid_rows['Labels'] == 'n-9']['Sample_ID'].values[0]
#         if sample_id_n7 == sample_id_n9:
#             intensity_n7 = lipid_rows[lipid_rows['Labels'] == 'n-7']['Intensity_OzESI'].values[0]
#             intensity_n9 = lipid_rows[lipid_rows['Labels'] == 'n-9']['Intensity_OzESI'].values[0]
            
#             # Extract scalar values from lists if they are in list format
#             if isinstance(intensity_n7, list) and len(intensity_n7) > 0:
#                 intensity_n7 = intensity_n7[0]
#             if isinstance(intensity_n9, list) and len(intensity_n9) > 0:
#                 intensity_n9 = intensity_n9[0]

#             # Check if the intensities are available and non-zero before dividing
#             if intensity_n7 and intensity_n9 and intensity_n7 != 0:
#                 intensity_ratio = round(intensity_n9 / intensity_n7, 2)  # rounding to 2 decimal places
#                 df.loc[lipid_rows[lipid_rows['Labels'] == 'n-7'].index, 'Ratio'] = intensity_ratio
#                 print(f'Lipid: {lipid}, Intensity Ratio (n-9/n-7): {intensity_ratio}')


df_matched_4 = df_matched_3_sorted.copy()
df_matched_4['Ratios'] = None
# unique_lipids = df_matched_4['Lipid'].unique()

# for lipid in unique_lipids:
#     lipid_rows = df_matched_4[df_matched_4['Lipid'] == lipid]

#     if 'n-7' in lipid_rows['Labels'].values and 'n-9' in lipid_rows['Labels'].values:
#         # Get all indices of 'n-7' and 'n-9' rows within the lipid group
#         n7_indices = lipid_rows[lipid_rows['Labels'] == 'n-7'].index
#         n9_indices = lipid_rows[lipid_rows['Labels'] == 'n-9'].index

#         for n7_idx in n7_indices:
#             for n9_idx in n9_indices:
#                 if lipid_rows.loc[n7_idx, 'Sample_ID'] == lipid_rows.loc[n9_idx, 'Sample_ID']:
#                     intensity_n7 = lipid_rows.loc[n7_idx, 'OzESI_Intensity']
#                     intensity_n9 = lipid_rows.loc[n9_idx, 'OzESI_Intensity']

#                     if isinstance(intensity_n7, list) and len(intensity_n7) > 0:
#                         intensity_n7 = intensity_n7[0]

#                     if isinstance(intensity_n9, list) and len(intensity_n9) > 0:
#                         intensity_n9 = intensity_n9[0]

#                     if intensity_n7 and intensity_n9 and intensity_n7 != 0:
#                         intensity_ratio = round(intensity_n9 / intensity_n7, 2)
#                         df_matched_4.loc[n7_idx, 'Ratio'] = intensity_ratio
#                         print(f"Lipid: {lipid}, Intensity Ratio (n-9/n-7): {intensity_ratio}")





def calculate_intensity_ratio(df):
    # Create a new column for ratios
    df['Ratios'] = pd.Series(dtype='float64')

    # Iterate through each row in the DataFrame
    for index, row in df.iterrows():
        lipid = row['Lipid']
        label = row['Labels']
        intensity = row['OzESI_Intensity']
        sample_id = row['Sample_ID']

        # Check if the label is n-9
        if label == 'n-9':
            # Find the corresponding row with n-7 label and same lipid name
            n7_row = df[(df['Lipid'] == lipid) & (df['Labels'] == 'n-7')& (df['Sample_ID'] == sample_id)]

            # If a matching row is found, calculate the intensity ratio
            if not n7_row.empty:
                n7_intensity = n7_row['OzESI_Intensity'].values[0]
                ratio = intensity / n7_intensity

                # Assign the ratio to the 'Ratios' column
                df.at[index, 'Ratios'] = ratio

    return df

df_matched_4 = calculate_intensity_ratio(df_matched_4)


In [34]:
df_matched_4.head(None)

Class      Intensity                        Lipid  Parent_Ion  \
27      TAG  686913.811157            [TG(50:3)]_FA18:1       846.8   
1440    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1441    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1442    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
1443    NaN  256799.577103            [TG(50:3)]_FA18:1       694.6   
...     ...            ...                          ...         ...   
58995   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58996   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58997   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58998   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   
58999   NaN   74964.065231  [TG(55:10),TG(54:3)]_FA18:1       820.8   

       Product_Ion                         Sample_ID      Transition  \
27           547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  846.8 -> 547.6   
1440         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1441         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1442         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
1443         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6   
...            ...                               ...             ...   
58995        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58996        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58997        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58998        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   
58999        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6   

       Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels  Ratios  
27              12.58          72587.0  764.8  736.8  694.8            NaN  
1440            11.69           3903.0  612.6  584.6  542.6   n-12     NaN  
1441            11.69           3903.0  612.6  584.6  542.6   n-12     NaN  
1442            11.69           3903.0  612.6  584.6  542.6   n-12     NaN  
1443            11.69           3903.0  612.6  584.6  542.6   n-12     NaN  
...               ...              ...    ...    ...    ...    ...     ...  
58995           14.65           1985.0  738.8  710.8  668.8    n-7     NaN  
58996           14.65           1985.0  738.8  710.8  668.8    n-7     NaN  
58997           14.65           1985.0  738.8  710.8  668.8    n-7     NaN  
58998           14.65           1985.0  738.8  710.8  668.8    n-7     NaN  
58999           14.65           1985.0  738.8  710.8  668.8    n-7     NaN  

[57920 rows x 14 columns]

In [35]:
#filtering df_matched for name but not removing the n-7 ratios
def sort_by_second_tg(lipid):
    tgs = lipid.split(',')
    if len(tgs) > 1:
        return tgs[1]
    else:
        return lipid

df_matched_4c = df_matched_4.copy()
df_matched_4c['Lipid'] = df_matched_4c['Lipid'].apply(sort_by_second_tg)
df_matched_4c.head(None)

Class      Intensity              Lipid  Parent_Ion  Product_Ion  \
27      TAG  686913.811157  [TG(50:3)]_FA18:1       846.8        547.6   
1440    NaN  256799.577103  [TG(50:3)]_FA18:1       694.6        547.6   
1441    NaN  256799.577103  [TG(50:3)]_FA18:1       694.6        547.6   
1442    NaN  256799.577103  [TG(50:3)]_FA18:1       694.6        547.6   
1443    NaN  256799.577103  [TG(50:3)]_FA18:1       694.6        547.6   
...     ...            ...                ...         ...          ...   
58995   NaN   74964.065231   TG(54:3)]_FA18:1       820.8        603.6   
58996   NaN   74964.065231   TG(54:3)]_FA18:1       820.8        603.6   
58997   NaN   74964.065231   TG(54:3)]_FA18:1       820.8        603.6   
58998   NaN   74964.065231   TG(54:3)]_FA18:1       820.8        603.6   
58999   NaN   74964.065231   TG(54:3)]_FA18:1       820.8        603.6   

                              Sample_ID      Transition  Retention_Time  \
27     DOD93_F4-5xFAD-Cereb_TG18-1_o3on  846.8 -> 547.6           12.58   
1440   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6           11.69   
1441   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6           11.69   
1442   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6           11.69   
1443   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  694.6 -> 547.6           11.69   
...                                 ...             ...             ...   
58995  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6           14.65   
58996  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6           14.65   
58997  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6           14.65   
58998  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6           14.65   
58999  FAD189_Ms-5xFAD-hippoTG18-1_o3on  820.8 -> 603.6           14.65   

       OzESI_Intensity    n-7    n-9   n-12 Labels  Ratios  
27             72587.0  764.8  736.8  694.8            NaN  
1440            3903.0  612.6  584.6  542.6   n-12     NaN  
1441            3903.0  612.6  584.6  542.6   n-12     NaN  
1442            3903.0  612.6  584.6  542.6   n-12     NaN  
1443            3903.0  612.6  584.6  542.6   n-12     NaN  
...                ...    ...    ...    ...    ...     ...  
58995           1985.0  738.8  710.8  668.8    n-7     NaN  
58996           1985.0  738.8  710.8  668.8    n-7     NaN  
58997           1985.0  738.8  710.8  668.8    n-7     NaN  
58998           1985.0  738.8  710.8  668.8    n-7     NaN  
58999           1985.0  738.8  710.8  668.8    n-7     NaN  

[57920 rows x 14 columns]

In [36]:
df_matched_4c.to_excel("df_matched_4c_04_29_23.xlsx")

In [37]:


# df_matched_4b= df_matched_4.sort_values(by=['Sample_ID', 'Lipid'], ascending=[True, True])

# def sort_by_second_tg(lipid):
#     tgs = lipid.split(',')
#     if len(tgs) > 1:
#         return tgs[1]
#     else:
#         return lipid

# df_matched_4b['Lipid'] = df_matched_4b['Lipid'].apply(sort_by_second_tg)

# df_matched_4b = df_matched_4b.sort_values(by='Ratios', ascending=False)
# # Remove duplicates based on Sample_ID and Lipid
# df_matched_4b = df_matched_4b.drop_duplicates(subset=['Sample_ID', 'Lipid'])
# df_matched_4b = df_matched_4b.sort_values(by='Sample_ID', ascending=True)
# df_matched_4b = df_matched_4b.sort_values(by=['Sample_ID', 'Lipid'], ascending=[True, True])

# df_matched_4b.to_excel("df_matched_4b_v4_04_29_23.xlsx")


In [38]:
# Filter rows where 'Ratios' column is not NaN
df_matched_5 = df_matched_4[df_matched_4['Ratios'].notna()]

# df_matched_5.to_excel("df_matched_5.xlsx")

In [39]:
df_matched_5.head(None)

Class      Intensity                        Lipid  Parent_Ion  \
1680    NaN  661318.406067            [TG(50:3)]_FA18:1       736.7   
1681    NaN  661318.406067            [TG(50:3)]_FA18:1       736.7   
1682    NaN  661318.406067            [TG(50:3)]_FA18:1       736.7   
1683    NaN  661318.406067            [TG(50:3)]_FA18:1       736.7   
1684    NaN  661318.406067            [TG(50:3)]_FA18:1       736.7   
...     ...            ...                          ...         ...   
58831   NaN  168453.170837  [TG(55:10),TG(54:3)]_FA18:1       792.8   
58833   NaN  168453.170837  [TG(55:10),TG(54:3)]_FA18:1       792.8   
58835   NaN  168453.170837  [TG(55:10),TG(54:3)]_FA18:1       792.8   
58837   NaN  168453.170837  [TG(55:10),TG(54:3)]_FA18:1       792.8   
58839   NaN  168453.170837  [TG(55:10),TG(54:3)]_FA18:1       792.8   

       Product_Ion                         Sample_ID      Transition  \
1680         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  736.7 -> 547.6   
1681         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  736.7 -> 547.6   
1682         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  736.7 -> 547.6   
1683         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  736.7 -> 547.6   
1684         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  736.7 -> 547.6   
...            ...                               ...             ...   
58831        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  792.8 -> 603.6   
58833        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  792.8 -> 603.6   
58835        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  792.8 -> 603.6   
58837        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  792.8 -> 603.6   
58839        603.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  792.8 -> 603.6   

       Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels    Ratios  
1680            12.52           9713.0  654.7  626.7  584.7    n-9  1.045533  
1681            12.52           9713.0  654.7  626.7  584.7    n-9  1.045533  
1682            12.52           9713.0  654.7  626.7  584.7    n-9  1.045533  
1683            12.52           9713.0  654.7  626.7  584.7    n-9  1.045533  
1684            12.52           9713.0  654.7  626.7  584.7    n-9  1.045533  
...               ...              ...    ...    ...    ...    ...       ...  
58831           14.66          17906.0  710.8  682.8  640.8    n-9  9.020655  
58833           14.66          17906.0  710.8  682.8  640.8    n-9  9.020655  
58835           14.66          17906.0  710.8  682.8  640.8    n-9  9.020655  
58837           14.66          17906.0  710.8  682.8  640.8    n-9  9.020655  
58839           14.66          17906.0  710.8  682.8  640.8    n-9  9.020655  

[20800 rows x 14 columns]

In [40]:
df_matched_6 = df_matched_5.copy()
# Assuming df_matched_5 is your DataFrame

df_matched_6 = df_matched_6.sort_values(by='Ratios', ascending=False)
# Remove duplicates based on Sample_ID and Lipid
df_matched_6 = df_matched_6.drop_duplicates(subset=['Sample_ID', 'Lipid'])
df_matched_6 = df_matched_6.sort_values(by='Sample_ID', ascending=True)

df_matched_6.head(None)


Class      Intensity                        Lipid  Parent_Ion  \
1790    NaN  936681.389038   [TG(51:8),TG(50:1)]_FA18:1       740.8   
1680    NaN  661318.406067            [TG(50:3)]_FA18:1       736.7   
2489    NaN  195273.793320  [TG(55:11),TG(54:4)]_FA18:1       790.8   
2647    NaN  748905.374359  [TG(55:10),TG(54:3)]_FA18:1       792.8   
1725    NaN  458210.334137   [TG(51:9),TG(50:2)]_FA18:1       738.7   
...     ...            ...                          ...         ...   
57874   NaN  229533.276276   [TG(51:9),TG(50:2)]_FA18:1       738.7   
58080   NaN   69821.684830            [TG(52:4)]_FA18:1       762.7   
57938   NaN  311655.842590   [TG(51:8),TG(50:1)]_FA18:1       740.8   
58123   NaN  938015.985718  [TG(53:10),TG(52:3)]_FA18:1       764.7   
57763   NaN  482563.335815            [TG(50:3)]_FA18:1       736.7   

       Product_Ion                         Sample_ID      Transition  \
1790         551.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  740.8 -> 551.6   
1680         547.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  736.7 -> 547.6   
2489         601.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  790.8 -> 601.6   
2647         603.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  792.8 -> 603.6   
1725         549.6  DOD93_F4-5xFAD-Cereb_TG18-1_o3on  738.7 -> 549.6   
...            ...                               ...             ...   
57874        549.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  738.7 -> 549.6   
58080        573.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  762.7 -> 573.6   
57938        551.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  740.8 -> 551.6   
58123        547.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  764.7 -> 547.6   
57763        547.6  FAD189_Ms-5xFAD-hippoTG18-1_o3on  736.7 -> 547.6   

       Retention_Time  OzESI_Intensity    n-7    n-9   n-12 Labels     Ratios  
1790            14.95         144069.0  658.8  630.8  588.8    n-9   1.729541  
1680            12.52           9713.0  654.7  626.7  584.7    n-9   1.045533  
2489            12.48          16153.0  708.8  680.8  638.8    n-9   4.583712  
2647            14.66         116813.0  710.8  682.8  640.8    n-9   4.507022  
1725            13.74          49935.0  656.7  628.7  586.7    n-9   3.244007  
...               ...              ...    ...    ...    ...    ...        ...  
57874           13.86           3831.0  656.7  628.7  586.7    n-9   1.701910  
58080           15.67            555.0  680.7  652.7  610.7    n-9   1.125761  
57938           14.95           9913.0  658.8  630.8  588.8    n-9   1.757313  
58123           15.79           8868.0  682.7  654.7  612.7    n-9  10.880982  
57763           15.94           4474.0  654.7  626.7  584.7    n-9   0.504511  

[360 rows x 14 columns]

In [41]:
df_matched_7 = df_matched_6.copy()
df_matched_7 = df_matched_7.sort_values(by=['Sample_ID', 'Lipid'], ascending=[True, True])

def sort_by_second_tg(lipid):
    tgs = lipid.split(',')
    if len(tgs) > 1:
        return tgs[1]
    else:
        return lipid

df_matched_7['Lipid'] = df_matched_7['Lipid'].apply(sort_by_second_tg)
df_matched_7 = df_matched_7.sort_values(by=['Sample_ID', 'Lipid'], ascending=[True, True])
df_matched_7.head(None)


Class     Intensity              Lipid  Parent_Ion  Product_Ion  \
1790    NaN  9.366814e+05   TG(50:1)]_FA18:1       740.8        551.6   
1725    NaN  4.582103e+05   TG(50:2)]_FA18:1       738.7        549.6   
2201    NaN  1.179938e+06   TG(52:2)]_FA18:1       766.7        577.6   
2091    NaN  2.812500e+05   TG(52:3)]_FA18:1       764.7        575.6   
2647    NaN  7.489054e+05   TG(54:3)]_FA18:1       792.8        603.6   
...     ...           ...                ...         ...          ...   
58783   NaN  1.684532e+05   TG(54:3)]_FA18:1       792.8        603.6   
58679   NaN  6.710156e+04   TG(54:4)]_FA18:1       790.8        601.6   
57763   NaN  4.825633e+05  [TG(50:3)]_FA18:1       736.7        547.6   
58080   NaN  6.982168e+04  [TG(52:4)]_FA18:1       762.7        573.6   
58513   NaN  5.632846e+04  [TG(54:5)]_FA18:1       788.8        599.6   

                              Sample_ID      Transition  Retention_Time  \
1790   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  740.8 -> 551.6           14.95   
1725   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  738.7 -> 549.6           13.74   
2201   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  766.7 -> 577.6           14.81   
2091   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  764.7 -> 575.6           13.59   
2647   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  792.8 -> 603.6           14.66   
...                                 ...             ...             ...   
58783  FAD189_Ms-5xFAD-hippoTG18-1_o3on  792.8 -> 603.6           14.66   
58679  FAD189_Ms-5xFAD-hippoTG18-1_o3on  790.8 -> 601.6           13.57   
57763  FAD189_Ms-5xFAD-hippoTG18-1_o3on  736.7 -> 547.6           15.94   
58080  FAD189_Ms-5xFAD-hippoTG18-1_o3on  762.7 -> 573.6           15.67   
58513  FAD189_Ms-5xFAD-hippoTG18-1_o3on  788.8 -> 599.6           12.48   

       OzESI_Intensity    n-7    n-9   n-12 Labels    Ratios  
1790          144069.0  658.8  630.8  588.8    n-9  1.729541  
1725           49935.0  656.7  628.7  586.7    n-9  3.244007  
2201          266662.0  684.7  656.7  614.7    n-9  2.697452  
2091           26821.0  682.7  654.7  612.7    n-9  1.428016  
2647          116813.0  710.8  682.8  640.8    n-9  4.507022  
...                ...    ...    ...    ...    ...       ...  
58783          17906.0  710.8  682.8  640.8    n-9  9.020655  
58679           1878.0  708.8  680.8  638.8    n-9  3.920668  
57763           4474.0  654.7  626.7  584.7    n-9  0.504511  
58080            555.0  680.7  652.7  610.7    n-9  1.125761  
58513            576.0  706.8  678.8  636.8    n-9  1.631728  

[360 rows x 14 columns]

In [42]:
df_matched_7.to_excel("df_matched_7.xlsx")

In [43]:

# Iterate through each row in the DataFrame
for index, row in df_matched_4c.iterrows():
    # Extract Lipid, Sample_ID, Labels and Ratios from the row
    lipid = row['Lipid']
    sample_id = row['Sample_ID']
    labels = row['Labels']
    ratios = row['Ratios']

    # Check if ratios is not NaN
    if not pd.isna(ratios):
        # Print out the values
        print(f'Lipid: {lipid}, Sample_ID: {sample_id}, Labels: {labels}, Ratios: {ratios}')


Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
Lipid: [TG(50:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Cereb_TG18-1_o3on, Labels: n-9, Ratios: 1.0455328310010765
L

Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA18:1, Sample_ID: DOD93_F4-5xFAD-Dienc_TG18-1_o3on, Labels: n-9, Ratios: 1.882001647446458
Lipid: TG(52:3)]_FA

In [44]:
def filter_highest_ratios(df):
    # Sort the DataFrame by ratios in descending order
    df_sorted = df.sort_values(by='Ratios', ascending=False)

    # Drop duplicates keeping the first occurrence (highest ratio)
    df_filtered = df_sorted.drop_duplicates(subset=['Sample_ID', 'Lipid','Labels'], keep='first')
    df_filtered = df_filtered.sort_values(by=['Sample_ID', 'Lipid'], ascending=[True, True])

    return df_filtered

df_matched_4d = filter_highest_ratios(df_matched_4c)


In [45]:
df_matched_4d.head(None)

Class     Intensity              Lipid  Parent_Ion  Product_Ion  \
1790    NaN  9.366814e+05   TG(50:1)]_FA18:1       740.8        551.6   
29      TAG  8.906404e+06   TG(50:1)]_FA18:1       850.8        551.6   
1520    NaN  6.608002e+06   TG(50:1)]_FA18:1       698.7        551.6   
2280    NaN  7.723013e+05   TG(50:1)]_FA18:1       768.8        551.6   
1725    NaN  4.582103e+05   TG(50:2)]_FA18:1       738.7        549.6   
...     ...           ...                ...         ...          ...   
58520   NaN  5.583928e+04  [TG(52:4)]_FA18:1       790.7        573.6   
58513   NaN  5.632846e+04  [TG(54:5)]_FA18:1       788.8        599.6   
1437    TAG  1.356127e+05  [TG(54:5)]_FA18:1       898.8        599.6   
57960   NaN  4.377910e+04  [TG(54:5)]_FA18:1       746.8        599.6   
58880   NaN  4.153152e+04  [TG(54:5)]_FA18:1       816.8        599.6   

                              Sample_ID      Transition  Retention_Time  \
1790   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  740.8 -> 551.6           14.95   
29     DOD93_F4-5xFAD-Cereb_TG18-1_o3on  850.8 -> 551.6           15.13   
1520   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  698.7 -> 551.6           14.00   
2280   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  768.8 -> 551.6           14.92   
1725   DOD93_F4-5xFAD-Cereb_TG18-1_o3on  738.7 -> 549.6           13.74   
...                                 ...             ...             ...   
58520  FAD189_Ms-5xFAD-hippoTG18-1_o3on  790.7 -> 573.6           14.06   
58513  FAD189_Ms-5xFAD-hippoTG18-1_o3on  788.8 -> 599.6           12.48   
1437   FAD189_Ms-5xFAD-hippoTG18-1_o3on  898.8 -> 599.6           12.43   
57960  FAD189_Ms-5xFAD-hippoTG18-1_o3on  746.8 -> 599.6           10.32   
58880  FAD189_Ms-5xFAD-hippoTG18-1_o3on  816.8 -> 599.6           11.37   

       OzESI_Intensity    n-7    n-9   n-12 Labels    Ratios  
1790          144069.0  658.8  630.8  588.8    n-9  1.729541  
29           2236988.0  768.8  740.8  698.8              NaN  
1520           59211.0  616.7  588.7  546.7   n-12       NaN  
2280           83299.0  686.8  658.8  616.8    n-7       NaN  
1725           49935.0  656.7  628.7  586.7    n-9  3.244007  
...                ...    ...    ...    ...    ...       ...  
58520            493.0  708.7  680.7  638.7    n-7       NaN  
58513            576.0  706.8  678.8  636.8    n-9  1.631728  
1437            4512.0  816.8  788.8  746.8              NaN  
57960            356.0  664.8  636.8  594.8   n-12       NaN  
58880            353.0  734.8  706.8  664.8    n-7       NaN  

[1518 rows x 14 columns]

In [46]:
df_matched_4d.to_excel("df_matched_4d.xlsx")

Visualizations

In [47]:
import plotly.express as px
import os

# Create the "Plots" directory if it doesn't exist
os.makedirs("Projects/04_29_23/Plots/filtered_lipids/", exist_ok=True)


# Define color mappings for Lipid patterns
color_mapping = {
    '50': 'red',
    '51': 'brown',
    '52': 'blue',
    '53': 'purple',
    '54': 'green',
}

# Get the unique Sample_IDs
sample_ids = df_matched_4d['Sample_ID'].unique()

# Loop over the unique Sample_IDs
for sample_id in sample_ids:
    
    # Filter the dataframe for the current Sample_ID
    df_sample = df_matched_4d[df_matched_4d['Sample_ID'] == sample_id]
    
    # Assign colors to Lipids based on patterns
    lipid_colors = []
    for lipid in df_sample['Lipid']:
        color = 'gray'  # Default color
        for pattern, pattern_color in color_mapping.items():
            if pattern in lipid:
                color = pattern_color
                break
        lipid_colors.append(color)
    
    # Create the bar plot
    fig = px.bar(df_sample, x='Lipid', y='Ratios', text='Ratios', title=f'Bar Plot for Sample_ID: {sample_id}',
                 color_discrete_map=color_mapping)
    
    # Apply colors to the bars
    fig.update_traces(
        marker_color=lipid_colors,
        texttemplate='%{text:.2f}',
        textposition='auto',
        marker_line_width=0
    )
    
    # Customize the layout
    fig.update_layout(
        uniformtext_minsize=18,
        uniformtext_mode='hide',
        xaxis=dict(
            title='Lipid',
            titlefont=dict(size=16)
        ),
        yaxis=dict(
            title='Ratios',
            titlefont=dict(size=16),
            tickfont=dict(size=16)  # Set the font size of y-axis labels
        ),
        legend=dict(
            title='Lipid Patterns',
            tracegroupgap=50,
            itemsizing='constant'
        ),
        title=dict(
            text=f'Sample_ID: {sample_id}',
            font=dict(size=20)  # Set the title font size
        )
    )
    # Save the plot as an image
    file_name = f"Projects/04_29_23/Plots/filtered_lipids//plot_{sample_id}.png"
    fig.write_image(file_name)
    
    # Show plot
    fig.show()


In [48]:
#########################

In [49]:
##########################
##########################
##########################
##########################
##########################
##########################

Caitlin Data

In [50]:
import pandas as pd


val_df = pd.read_excel("Caitlin.xlsx", header=1)
val_df = val_df.rename(columns={'Ratio n-9/n-7': 'Ratios'})
val_df.head(None)

Lipid     MRM Identity MRM Transition    RT  Relative Abundance %  \
0    TG 50:1  TG 50:1_FA 18:1    850.8→551.6    15             16.441215   
1    TG 50:2  TG 50:2_FA 18:1    850.8→549.6  13.8              4.155703   
2    TG 50:3  TG 50:3_FA 18:1    846.8→547.6  12.5              0.375821   
3    TG 52:2  TG 52:2_FA 18:1    876.8→547.6  14.8             41.588725   
4    TG 52:3  TG 52:3_FA 18:1    874.8→575.6  13.7              7.943199   
..       ...              ...            ...   ...                   ...   
112  TG 52:3  TG 52:3_FA 18:1    874.8→575.6  13.7             12.187151   
113  TG 52:4  TG 52:4_FA 18:1    872.8→573.6    nd              1.459308   
114  TG 54:3  TG 54:3_FA 18:1    902.8→603.6  14.7             22.415748   
115  TG 54:4  TG 54:4_FA 18:1    900.8→601.6  13.5             10.833710   
116  TG 54:5  TG 54:5_FA 18:1    898.8→599.6  12.4              2.568531   

     n-9 isomer %  n-7 isomer %    Ratios                   Sample_ID  
0       67.910997     32.089003  2.116332  DOD93 5xFAD F4 Hippocampus  
1       76.970166     23.029834  3.342194  DOD93 5xFAD F4 Hippocampus  
2             NaN           NaN       NaN  DOD93 5xFAD F4 Hippocampus  
3       69.849531     30.150469  2.316698  DOD93 5xFAD F4 Hippocampus  
4       77.032611     22.967389  3.354000  DOD93 5xFAD F4 Hippocampus  
..            ...           ...       ...                         ...  
112     87.409386     12.590614  6.942424  FAD 184 F4 WT Cerebellum    
113           NaN           NaN       NaN  FAD 184 F4 WT Cerebellum    
114     88.152261     11.847739  7.440429  FAD 184 F4 WT Cerebellum    
115    100.000000      0.000000       NaN  FAD 184 F4 WT Cerebellum    
116    100.000000      0.000000       NaN  FAD 184 F4 WT Cerebellum    

[117 rows x 9 columns]

In [51]:
import plotly.express as px

# Assuming val_df is your DataFrame after renaming the column
fig = px.scatter(val_df, x="Lipid", y="Ratios", color="Sample_ID",
                 title="Lipid vs Ratios for each Sample_ID",
                 labels={"Lipid": "Lipid", "Ratios": "Ratios"},
                 hover_data=["Sample_ID"])

fig.show()



In [52]:
import plotly.express as px

# Assuming val_df is your DataFrame after renaming the column
caitlin = val_df["Sample_ID"].unique()
me = df_matched_4d["Sample_ID"].unique()

for sample_id in caitlin:
    # Filter the DataFrame for the current Sample_ID
    sample_df = val_df[val_df["Sample_ID"] == sample_id]
    
    # Create scatter plot for the current Sample_ID
    fig = px.scatter(sample_df, x="Lipid", y="Ratios",
                     title=f"Lipid vs Ratios for Sample_ID: {sample_id}",
                     labels={"Lipid": "Lipid", "Ratios": "Ratios"},
                     hover_data=["Sample_ID"])
    
    # Display the figure
    fig.show()


In [53]:
import plotly.graph_objects as go

# Assuming val_df and df_matched_4d are your DataFrames
caitlin = val_df["Sample_ID"].unique()
me = df_matched_4d["Sample_ID"].unique()

# Create new column 'Source' to differentiate the data from two DataFrames
val_df["Source"] = "Caitlin"
df_matched_4d["Source"] = "Me"

# Append the two dataframes
combined_df = pd.concat([val_df, df_matched_4d])

for sample_id in set(list(caitlin) + list(me)):  # Combining unique sample IDs from both dataframes
    # Filter the DataFrame for the current Sample_ID
    sample_df = combined_df[combined_df["Sample_ID"] == sample_id]

    # Create scatter plot for Caitlin data
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=sample_df[sample_df['Source'] == 'Caitlin']["Lipid"],
                             y=sample_df[sample_df['Source'] == 'Caitlin']["Ratios"],
                             mode='markers',
                             name='Caitlin'))

    # Create scatter plot for Me data
    fig.add_trace(go.Scatter(x=sample_df[sample_df['Source'] == 'Me']["Lipid"],
                             y=sample_df[sample_df['Source'] == 'Me']["Ratios"],
                             mode='markers',
                             name='Me'))

    fig.update_layout(title=f"Lipid vs Ratios for Sample_ID: {sample_id}",
                      xaxis_title="Lipid",
                      yaxis_title="Ratios")

    # Display the figure
    fig.show()


In [55]:
import pandas as pd

# Adding a new column 'Person' to indicate the source of data
val_df['Person'] = 'Caitlin'
df_matched_4d['Person'] = 'Me'

# Selecting only the required columns
val_df = val_df[['Lipid', 'Ratios', 'Sample_ID', 'Person']]
df_matched_4d = df_matched_4d[['Lipid', 'Ratios', 'Sample_ID', 'Person']]

# Concatenating the two DataFrames
validation = pd.concat([val_df, df_matched_4d], ignore_index=True)

# Displaying the combined DataFrame
validation.head(None)

Lipid    Ratios                         Sample_ID   Person
0               TG 50:1  2.116332        DOD93 5xFAD F4 Hippocampus  Caitlin
1               TG 50:2  3.342194        DOD93 5xFAD F4 Hippocampus  Caitlin
2               TG 50:3       NaN        DOD93 5xFAD F4 Hippocampus  Caitlin
3               TG 52:2  2.316698        DOD93 5xFAD F4 Hippocampus  Caitlin
4               TG 52:3  3.354000        DOD93 5xFAD F4 Hippocampus  Caitlin
...                 ...       ...                               ...      ...
1630  [TG(52:4)]_FA18:1       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me
1631  [TG(54:5)]_FA18:1  1.631728  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me
1632  [TG(54:5)]_FA18:1       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me
1633  [TG(54:5)]_FA18:1       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me
1634  [TG(54:5)]_FA18:1       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me

[1635 rows x 4 columns]

In [68]:

# Mapping for 3-letter codes
keywords_mapping = {
    'hippocampus': 'HIP',
    'hippo': 'HIP',
    'cortex': 'COR',
    'cort': 'COR',
    'cerebellum': 'CER',
    'cereb': 'CER',
    'diencephalon': 'DIE',
    'dienc': 'DIE'
}
additional_keywords = ['DOD93', 'DOD94', 'FAD185', 'FAD189']

# Function to get additional ID based on keywords
def get_additional_id(sample_id):
    for keyword in additional_keywords:
        if keyword.lower() in sample_id.lower():
            return keyword
    return None

# Create the new 'ID' column
validation['ID'] = validation['Sample_ID'].apply(get_id)

# Create the new 'ID_2' column
validation['ID_2'] = validation['Sample_ID'].apply(get_additional_id)



import re

def reformat_lipid_name(lipid_name):
    # Find pattern like TG(50:1) within the string
    match = re.search(r'\b([A-Z]{2})\((\d+:\d+)\)', lipid_name)
    # If the pattern is found, reformat it as 'TG 50:1'
    if match:
        return f"{match.group(1)} {match.group(2)}"
    # If the pattern is not found, return the original string
    return lipid_name

# Apply the transformation to each entry in the 'Lipid' column
validation['Lipid'] = validation['Lipid'].apply(reformat_lipid_name)
def extract_f3_f4(sample_id):
    # Check if 'F3' or 'F4' is in the Sample_ID and return it
    if 'F3' in sample_id:
        return 'F3'
    elif 'F4' in sample_id:
        return 'F4'
    else:
        return None

# Create a new column 'ID_3' in the DataFrame
validation['ID_3'] = validation['Sample_ID'].apply(extract_f3_f4)


# validation.to_excel("validation.xlsx")
# Display the DataFrame
validation.head(None)

Lipid    Ratios                         Sample_ID   Person   ID  \
0     TG 50:1  2.116332        DOD93 5xFAD F4 Hippocampus  Caitlin  HIP   
1     TG 50:2  3.342194        DOD93 5xFAD F4 Hippocampus  Caitlin  HIP   
2     TG 50:3       NaN        DOD93 5xFAD F4 Hippocampus  Caitlin  HIP   
3     TG 52:2  2.316698        DOD93 5xFAD F4 Hippocampus  Caitlin  HIP   
4     TG 52:3  3.354000        DOD93 5xFAD F4 Hippocampus  Caitlin  HIP   
...       ...       ...                               ...      ...  ...   
1630  TG 52:4       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me  HIP   
1631  TG 54:5  1.631728  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me  HIP   
1632  TG 54:5       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me  HIP   
1633  TG 54:5       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me  HIP   
1634  TG 54:5       NaN  FAD189_Ms-5xFAD-hippoTG18-1_o3on       Me  HIP   

        ID_2  ID_3  
0      DOD93    F4  
1      DOD93    F4  
2      DOD93    F4  
3      DOD93    F4  
4      DOD93    F4  
...      ...   ...  
1630  FAD189  None  
1631  FAD189  None  
1632  FAD189  None  
1633  FAD189  None  
1634  FAD189  None  

[1635 rows x 7 columns]

In [65]:
import plotly.express as px

# Fill NaN values in the 'ID' and 'ID_2' columns with a default value
validation['ID'] = validation['ID'].fillna('UNKNOWN')
validation['ID_2'] = validation['ID_2'].fillna('UNKNOWN')

# Create scatter plot
fig = px.scatter(validation, x="Lipid", y="Ratios", color="Person",
                 facet_col="ID", facet_row="ID_2", 
                 title="Lipid vs Ratios for each ID and ID_2",
                 labels={"Lipid": "Lipid", "Ratios": "Ratios"},
                 hover_data=["Sample_ID"])

# Display the figure
fig.show()



In [71]:
import plotly.express as px
save_dir = "Projects/04_29_23/Plots/validation/"
# Fill NaN values in the 'ID', 'ID_2', and 'ID_3' columns with a default value
validation['ID'] = validation['ID'].fillna('UNKNOWN')
validation['ID_2'] = validation['ID_2'].fillna('UNKNOWN')
validation['ID_3'] = validation['ID_3'].fillna('UNKNOWN')

# Loop through unique combinations of ID, ID_2, and ID_3
unique_ids = validation[['ID', 'ID_2', 'ID_3']].drop_duplicates().values

for id1, id2, id3 in unique_ids:
    # Filter the DataFrame for the current ID, ID_2, and ID_3
    filtered_df = validation[(validation['ID'] == id1) & (validation['ID_2'] == id2) & (validation['ID_3'] == id3)]

    # Create scatter plot for the current ID, ID_2, and ID_3
    fig = px.scatter(filtered_df, x="Lipid", y="Ratios", color="Person",
                     title=f"Lipid vs Ratios for ID: {id1}, ID_2: {id2}, ID_3: {id3}",
                     labels={"Lipid": "Lipid", "Ratios": "Ratios"},
                     hover_data=["Sample_ID"])
    # Save the figure as PNG
    save_path = os.path.join(save_dir, f"plot_{id1}_{id2}_{id3}.png")
    fig.write_image(save_path, format='png')

    # Display the figure
    fig.show()
